In [2]:
from Bio.Seq import Seq
from tqdm import tqdm
import numpy as np

# GenAI model used in this code: Claude 3.5 Sonnet

# Read the FASTA file

In [3]:
# Prompt: Write a Python function to read a FASTA file and extract the DNA sequence, skipping header lines.

def read_fasta(file_path):
    """
    Reads a FASTA file and extracts the sequence.
    
    Args:
    file_path (str): Path to the FASTA file.
    
    Returns:
    str: The extracted DNA sequence.
    """
    with open(file_path, 'r') as f:
        sequence = ""
        for line in f:
            if not line.startswith('>'):  # Skip header lines
                sequence += line.strip()
    return sequence

In [4]:
# Get the FASTA file path from command-line argument
fasta_file = 'small.fna'    
# Read the FASTA file and extract the sequence
sequence = read_fasta(fasta_file)

# Question 1

In [5]:
# Prompt: Write a Python function to find all ORFs in a DNA sequence using NumPy.

def find_orfs_numpy_q_1(sequence):
    stop_codons = ['TAA', 'TAG', 'TGA']
    chars = np.array(list(sequence))
    n_codons = len(chars) // 3
    if n_codons == 0:
        return []
    codons = chars[:n_codons*3].reshape(-1, 3)
    codon_strings = np.array([''.join(codon) for codon in codons])
    start_indices = np.where(codon_strings == 'ATG')[0]
    stop_indices = np.where(np.isin(codon_strings, stop_codons))[0]

    orfs = []
    if len(start_indices) == 0 or len(stop_indices) == 0:
        return orfs

    # For each start_index, find the index in stop_indices where stop_idx >= start_idx
    idx_positions = np.searchsorted(stop_indices, start_indices, side='left')

    for i, start_idx in enumerate(start_indices):
        stop_idx_pos = idx_positions[i]
        # Ensure that the stop index is within bounds
        if stop_idx_pos < len(stop_indices):
            stop_idx = stop_indices[stop_idx_pos]
            if stop_idx >= start_idx:
                orf_codons = codon_strings[start_idx:stop_idx+1]
                orf_seq = ''.join(orf_codons)
                orfs.append(orf_seq)
    return orfs

In [12]:
orfs_for_q1 = find_orfs_numpy_q_1(sequence)
for orf in orfs_for_q1:
    print(orf)

ATGTTTTACGATGGTCCTCAGGTAGCGAATCTCCAGAACGTCGACACTGGTTTTTGGCTGGACATGAGCAATCTCTCAGACGTTGTATTATCCAGAGAGATTCAAACAGGACTTCGAGCACGAGCTACTTTGGAAGAATCCATGCCGATGTTAGAGAATTTAGAAGAGCGTTTTAGACGTTTGCAAGAAACTTGTGATGCGGCTCGTACTGAGATAGAAGAATCGGGATGGACTCGAGAGTCCGCATCAAGAATGGAAGGCGATGAGGCGCAAGGACCTTCTAGAGCACAACAAGCTTTTCAGAGCTTTGTAAATGAATGTAACAGCATCGAGTTCTCATTTGGGAGCTTTGGAGAGCATGTGCGAGTTCTCTGCGCTAGAGTATCACGAGGATTAGCTGCCGCAGGAGAGGCGATTCGCCGTTGCTTCTCTTGTTGTAAAGGATCGACGCATCGCTACGCTCCTCGCGATGACCTATCTCCTGAAGGTGCATCGTTAGCAGAGACTTTGGCTAGATTCGCAGATGATATGGGAATAGAGCGAGGTGCTGATGGAACCTACGATATTCCTTTGGTAGATGATTGGAGAAGAGGGGTTCCTAGTATTGAAGGAGAAGGATCTGACTCGATCTATGAAATCATGATGCCTATCTATGAAGTTATGGATATGGATCTAGAAACACGAAGATCTTTTGCGGTACAGCAAGGGCACTATCAGGACCCAAGAGCTTCAGATTATGACCTCCCACGTGCTAGCGACTATGATTTGCCTAGAAGCCCATATCCTACTCCACCTTTGCCTCCTAGATATCAGCTACAGAATATGGATGTAGAAGCAGGGTTCCGTGAGGCAGTTTATGCTTCTTTTGTAGCAGGAATGTACAATTATGTAGTGACACAGCCGCAAGAGCGTATTCCCAATAGTCAGCAGGTGGAAGGGATTCTGCGTGATATGCTTACCAACGGGTCACAGACATTTAGAGACCTGATGAGGCGTTGGA

# Question 2


In [6]:
# Prompt: Write a Python function to find ORFs in all six reading frames of a DNA sequence, using a given ORF-finding function.

# The function has been manually modified to suit different problems by adding parameters and branching structure.
def find_orfs_in_frames(sequence, func, frames, min_length=None):
    orfs = []
    for frame in frames:
        if min_length is not None:
            orfs += func(sequence, frame, min_length)
        elif func == find_orfs_numpy_q_1:
            orfs += func(sequence)
        else:
            orfs += func(sequence, frame)
    return orfs

def find_orfs_in_six_frames(sequence, func, min_length=None):
    frames = [0, 1, 2]
    orfs = find_orfs_in_frames(sequence, func, frames, min_length)
    reverse_complement = str(Seq(sequence).reverse_complement()) # 关键点：反向互补
    orfs += find_orfs_in_frames(reverse_complement, func, frames, min_length)
    return orfs

In [7]:
orfs_for_q2 = find_orfs_in_six_frames(sequence,find_orfs_numpy_q_1)
for orf in orfs_for_q2:
    print(orf)

ATGTTTTACGATGGTCCTCAGGTAGCGAATCTCCAGAACGTCGACACTGGTTTTTGGCTGGACATGAGCAATCTCTCAGACGTTGTATTATCCAGAGAGATTCAAACAGGACTTCGAGCACGAGCTACTTTGGAAGAATCCATGCCGATGTTAGAGAATTTAGAAGAGCGTTTTAGACGTTTGCAAGAAACTTGTGATGCGGCTCGTACTGAGATAGAAGAATCGGGATGGACTCGAGAGTCCGCATCAAGAATGGAAGGCGATGAGGCGCAAGGACCTTCTAGAGCACAACAAGCTTTTCAGAGCTTTGTAAATGAATGTAACAGCATCGAGTTCTCATTTGGGAGCTTTGGAGAGCATGTGCGAGTTCTCTGCGCTAGAGTATCACGAGGATTAGCTGCCGCAGGAGAGGCGATTCGCCGTTGCTTCTCTTGTTGTAAAGGATCGACGCATCGCTACGCTCCTCGCGATGACCTATCTCCTGAAGGTGCATCGTTAGCAGAGACTTTGGCTAGATTCGCAGATGATATGGGAATAGAGCGAGGTGCTGATGGAACCTACGATATTCCTTTGGTAGATGATTGGAGAAGAGGGGTTCCTAGTATTGAAGGAGAAGGATCTGACTCGATCTATGAAATCATGATGCCTATCTATGAAGTTATGGATATGGATCTAGAAACACGAAGATCTTTTGCGGTACAGCAAGGGCACTATCAGGACCCAAGAGCTTCAGATTATGACCTCCCACGTGCTAGCGACTATGATTTGCCTAGAAGCCCATATCCTACTCCACCTTTGCCTCCTAGATATCAGCTACAGAATATGGATGTAGAAGCAGGGTTCCGTGAGGCAGTTTATGCTTCTTTTGTAGCAGGAATGTACAATTATGTAGTGACACAGCCGCAAGAGCGTATTCCCAATAGTCAGCAGGTGGAAGGGATTCTGCGTGATATGCTTACCAACGGGTCACAGACATTTAGAGACCTGATGAGGCGTTGGA

# Question 3 (Rosalind 72)

In [8]:
# Prompt: Modify the previous find_orfs_numpy_q_1 function to find Open Reading Frames (ORFs) in a DNA sequence. 
# The function should be able to handle different reading frames

def find_orfs_numpy_q_3_4(sequence,frame=0):
    stop_codons = ['TAA', 'TAG', 'TGA']
    sequence = sequence[frame:]
    chars = np.array(list(sequence))
    n_codons = len(chars) // 3
    if n_codons == 0:
        return []
    codons = chars[:n_codons*3].reshape(-1, 3)
    codon_strings = np.array([''.join(codon) for codon in codons])
    start_indices = np.where(codon_strings == 'ATG')[0]
    stop_indices = np.where(np.isin(codon_strings, stop_codons))[0]

    orfs = []
    if len(start_indices) == 0 or len(stop_indices) == 0:
        return orfs

    # For each start_index, find the index in stop_indices where stop_idx >= start_idx
    idx_positions = np.searchsorted(stop_indices, start_indices, side='left')

    for i, start_idx in enumerate(start_indices):
        stop_idx_pos = idx_positions[i]
        # Ensure that the stop index is within bounds
        if stop_idx_pos < len(stop_indices):
            stop_idx = stop_indices[stop_idx_pos]
            if stop_idx >= start_idx:
                orf_codons = codon_strings[start_idx:stop_idx+1]
                orf_seq = ''.join(orf_codons)
                orfs.append(orf_seq)
    return orfs

In [9]:
# Prompt: Create a function that takes a list of ORFs (DNA sequences) as input and returns a set of unique protein sequences. 
# The function should use the Biopython Seq class to translate each ORF. 
# Use tqdm to show a progress bar during translation.

def translate_orfs(orfs):
    """
    Translates a list of ORFs to protein sequences.
    
    Args:
    orfs (list): A list of DNA sequences representing ORFs.
    
    Returns:
    set: A set of unique protein sequences.
    """
    protein_strings = set()
    for orf in tqdm(orfs, desc="Translating ORFs"):
        protein = Seq(orf).translate(to_stop=True)
        protein_strings.add(str(protein))
    return protein_strings

In [11]:
sequence_rosalind_72 = read_fasta('rosalind_orf.txt')
orfs_for_q3_4 = find_orfs_in_six_frames(sequence_rosalind_72,find_orfs_numpy_q_3_4)
protein_strings_for_q3_4 = translate_orfs(orfs_for_q3_4)
for orf in protein_strings_for_q3_4:
    print(orf)

Translating ORFs: 100%|██████████| 26/26 [00:00<00:00, 25860.07it/s]

MRYRSPLADMGSND
MYGHVSDNLVPAAR
MLCRVLLSHDELEACLMAPSR
MFGHAMQSIAESRRIRGLSNGTQSLTEPQPGDS
MSASGDLYRIAKVCYVWTCYAEYC
MSKHSRLLLCDTGLH
MYTLNLIGCWGSSQLHTLQQYGC
MYKQTEGLSRCNFPRRFSA
MQSPTQYAQIHTWKPGHTV
MLKYILGSRDTRSSVYLTAKAVTLEHKIR
MRTLAPNRLIPCQLVETCIA
MYLSILGR
MSVMELCTL
ML
MGSND
MHVVATTCITP
MRVYRRCIVQLILALKH
MAPSR
MELCTL
MID
MNGHSKGPS
MQSIAESRRIRGLSNGTQSLTEPQPGDS
MTAL


# Question 4

To run it through command line, use `week3-question4.py` file, then run `find . -type f -name "*.fna" -exec python week3-question4.py {} \;` (For Windows please use `gci -r *.fna | % { python week3-question4.py $_.FullName }`).

In [28]:
import os
import platform

def search_and_process_fna_files():
    for root, dirs, files in os.walk('.'):
        for file in files:
            if file.endswith('.fna'):
                file_path = os.path.join(root, file)
                sequence = read_fasta(file_path)
                orfs_six_frames = find_orfs_in_six_frames(sequence, find_orfs_numpy_q_3_4)
                protein_strings = translate_orfs(orfs_six_frames)
                print(f"Handling file: {file_path}")
                print(f"Number of protein sequences found: {len(protein_strings)}")
                print("---")

print("Running on {}",platform.system())
search_and_process_fna_files()

Running on Windows


Translating ORFs: 100%|██████████| 33/33 [00:00<00:00, 41892.26it/s]

Handling file: .\rosalind_orf.fna
Number of protein sequences found: 32
---



Translating ORFs: 100%|██████████| 32142/32142 [00:00<00:00, 39084.05it/s]

Handling file: .\small.fna
Number of protein sequences found: 27933
---


# Question 5

In [29]:
# Prompt: Modify the find_orfs_numpy_q_3_4 function to include a minimum length filter for ORFs.The function should now:
# 1. Accept a 'min_length' parameter (default 100)
# 2. Only include ORFs that are at least 'min_length' codons long

def find_orfs_numpy_q5(sequence, min_length=100,frame=0):
    stop_codons = ['TAA', 'TAG', 'TGA']
    sequence = sequence[frame:]
    chars = np.array(list(sequence))
    n_codons = len(chars) // 3
    if n_codons == 0:
        return []
    codons = chars[:n_codons*3].reshape(-1, 3)
    codon_strings = np.array([''.join(codon) for codon in codons])
    start_indices = np.where(codon_strings == 'ATG')[0]
    stop_indices = np.where(np.isin(codon_strings, stop_codons))[0]

    orfs = []
    if len(start_indices) == 0 or len(stop_indices) == 0:
        return orfs

    # For each start_index, find the index in stop_indices where stop_idx >= start_idx
    idx_positions = np.searchsorted(stop_indices, start_indices, side='left')

    for i, start_idx in enumerate(start_indices):
        stop_idx_pos = idx_positions[i]
        # Ensure that the stop index is within bounds
        if stop_idx_pos < len(stop_indices):
            stop_idx = stop_indices[stop_idx_pos]
            if stop_idx >= start_idx:
                orf_length = stop_idx - start_idx + 1
                if orf_length >= min_length: # ORF min_length
                    orf_codons = codon_strings[start_idx:stop_idx+1]
                    orf_seq = ''.join(orf_codons)
                    orfs.append(orf_seq)
    return orfs

In [30]:
orfs_for_q5 = find_orfs_in_six_frames(sequence,find_orfs_numpy_q5,min_length=100)
protein_strings_for_q5 = translate_orfs(orfs_for_q5)
for orf in protein_strings_for_q5:
    print(orf)

Translating ORFs: 100%|██████████| 31743/31743 [00:00<00:00, 37999.95it/s]

MDNGVLDIRSLSIKVFYAQLSCASGLFVQIVLVFCSRSKTFILSAAFLFAFILVIVKNVEKLLVAILSDRFFVRKTRVIVLQNNMSRT
MIDS
MHTQRLIYRLKRTLSPLHCK
MLPRPLPSAPFSLVAYHKVL
MLIKTVLGVLYMKLPHQLVTIFLRYDRSCGYRYGTSIPFYNLKRRNFMRQKQPVNQ
MELSCGYGVTIQLLLQNDPRQSCLRNLFFWMESTLTPVILLDIAERHWPALWDRVLGLGMRITTPSVYREERARVSESNSQAVELFGDDRRDRYRSRQHAAVGTSVELVSVVCGALVQLMFLGIDGFSLRLPEICREVPCNNTSTPNSTVIANSTTPSLNNTSTCSGNSTTRPVLPSITGIYETDVQTTGVARTLNVIRMIWCGVMLLYFLYTAFRLVRNARRRN
MRISYFLQ
MSKYLMLL
MEGL
MRVDLLSVSCLELKKLMELAPISILAWKKPESCSQADWIDKMQSLAELNPNYLDLEKDFPEEDMIRIRQLHPQIKIIRSLHTSEHTDIIQLYAHMRSSAADYYKFAVSSSSTTDLLDICHQKRSLPENTTVVCLGGMGRPSRILSPILQNPFTYARSTGSSPVAPGQFSLKHHYFYNFASLSAQSPICALIGDTSRSIGHLTHNPFFSQLGVACPYIKLPLTPQELPKFFSTIRTQPFLGVSVTSPLKTAVLPFLDKQAPSVKASGSCNTLVIRQGEIEGHDTDGEGLFSVLMQHQIPLNNQRVAIIGAGGAAQSIATRLSRANCELLIFNRTKAHAEDLASRCQAKAFSLEELPLHRVSLIINCLPPSCTIPKAVAPCVVDINTIPKHSTFTQYARSQGSSIIYGHEMFTQQALLQFRLWFPTLSFKHLEKTFIRRAAVLASLFSIAP
MLIRIGEYRRGSDREVDFAIDHIDKLNRFLKQDIHEKTNYEEAAQQLRAIFR
MWEVCTHYSVNRRNAPRLFLFRRRQG
MLNRLRRHVHRIISFPSEKICSCLFY
M

# Question 6

In [34]:
def has_shine_dalgarno(upstream_seq):
    sd_sequence = "AGGAGG"
    return sd_sequence in upstream_seq

In [32]:
# Prompt: Modify the find_orfs_numpy_q5 function to include a check for the Shine-Dalgarno sequence upstream of each potential ORF.
# The function should:
# 1. For each potential ORF, Use the has_shine_dalgarno function defined aboved to check the upstream sequence (20 nucleotides before the start codon) for the Shine-Dalgarno sequence
# 2. Only include ORFs that have the Shine-Dalgarno sequence in the final output

def find_orfs_numpy_q6(sequence, min_length=100,frame=0):
    stop_codons = ['TAA', 'TAG', 'TGA']
    sequence = sequence[frame:]
    chars = np.array(list(sequence))
    n_codons = len(chars) // 3
    if n_codons == 0:
        return []
    codons = chars[:n_codons*3].reshape(-1, 3)
    codon_strings = np.array([''.join(codon) for codon in codons])
    start_indices = np.where(codon_strings == 'ATG')[0]
    stop_indices = np.where(np.isin(codon_strings, stop_codons))[0]

    orfs = []
    if len(start_indices) == 0 or len(stop_indices) == 0:
        return orfs

    # For each start_index, find the index in stop_indices where stop_idx >= start_idx
    idx_positions = np.searchsorted(stop_indices, start_indices, side='left')

    for i, start_idx in enumerate(start_indices):
        stop_idx_pos = idx_positions[i]
        # Ensure that the stop index is within bounds
        if stop_idx_pos < len(stop_indices):
            stop_idx = stop_indices[stop_idx_pos]
            if stop_idx >= start_idx:
                orf_length = stop_idx - start_idx + 1
                if orf_length >= min_length: # ORF min_length
                    # Check if the ORF has a Shine-Dalgarno sequence
                    upstream_start = max(0, start_idx * 3 - 20)
                    upstream_seq = sequence[upstream_start:start_idx * 3]
                    if has_shine_dalgarno(upstream_seq):
                        orf_codons = codon_strings[start_idx:stop_idx+1]
                        orf_seq = ''.join(orf_codons)
                        orfs.append(orf_seq)
    return orfs

In [35]:
orfs_for_q6 = find_orfs_in_six_frames(sequence,find_orfs_numpy_q6,min_length=100)
protein_strings_for_q6 = translate_orfs(orfs_for_q6)
for orf in protein_strings_for_q6:
    print(orf)

Translating ORFs: 100%|██████████| 153/153 [00:00<00:00, 25194.48it/s]

MYGFSLKPTRLPSESSELAPEAVTPGLVLSYQELLYEAEEDLKEVEGLLAQKSKDLELAQKKIEQLQSGLKCVLEESLI
MACWLFNQEKERVS
MG
MGIKPHDHGCWGSRGNIFTLQDLDTQQANQSAAASSSSVLKSECTAKVARYALGFLFGLGFILSIVTFIAAAATLPLGTVTILIMVTQAAFAAALAFKLYDLFKHDVPTCSITSKA
MLAACIIFVFRVYR
MGWIALRLLATLQ
MTTISGEGRFSFRLQNCFASSKNTSISTELS
MGGMGALFLSKQ
MFLQQKFLMYLEIWVLPFFRLLKGF
MIWGLDRMSLEMKLFKKV
MYLIIMCCMDWGQRVSITT
MEKPCYVLSKNMEKNIVYIVRGEDHPLLYRQELLAKELNWFVPLQEPMICSAKVRYRSPDEKCSVYPLEDGTVKVIFDVPVKAVTPGQTVAFYQGDICLGGGVIEVPMIHQL
MTRTFLAISSPALSLEKNGHKCTQKRCKKSLESKL
MLLLPEEEIVKIFKENCTLQNFILTV
MTQKTFPCISH
M
MVIVYDFEELSYQEPPLRFEAGTPHIAGVLGLGAAIDYLQALPFSITDRLTELTHFLYEQLLTVPGIQIIGPKQGAARGSLCSISIPGVQASDLGFLLDGRGISVRSGHQCSQPAMVRWDLGHVLRASLGIYNEQQDILLFVEALKDILRAYRS
MTTPDNNTIDVSFPTFVRLNVATTDLADGNKSNAVTITETATANYVNVTQDLTSSTAKLECTQDLIAQGKLIVTNPKSDISFGGRVNLADNTVNYSNGGAEVSFTNINSRQGKQYVPYGLYKNGEPKISMRSALSGGHVGSGDTGGWGAEVLWDAYTEQLKDMTDGAVTLNSSNRGKLSFTASPEAPVLFRLSVFMRKNGDWLDNGVGGRVMLYVNTTDSAGKTVRRLLGIAVCLGSTWYTTVPMFWCAATYYATSSGFFQLIVGERNFRVSSLSWSVVRLPVVP
MFS
MR
MLCPFCNH